<img align="left" src="https://lever-client-logos.s3.amazonaws.com/864372b1-534c-480e-acd5-9711f850815c-1524247202159.png" width=200>
<br></br>
<br></br>

## *Data Science Unit 4 Sprint 3 Assignment 1*

# Recurrent Neural Networks and Long Short Term Memory (LSTM)

![Monkey at a typewriter](https://upload.wikimedia.org/wikipedia/commons/thumb/3/3c/Chimpanzee_seated_at_typewriter.jpg/603px-Chimpanzee_seated_at_typewriter.jpg)

It is said that [infinite monkeys typing for an infinite amount of time](https://en.wikipedia.org/wiki/Infinite_monkey_theorem) will eventually type, among other things, the complete works of Wiliam Shakespeare. Let's see if we can get there a bit faster, with the power of Recurrent Neural Networks and LSTM.

This text file contains the complete works of Shakespeare: https://www.gutenberg.org/files/100/100-0.txt

Use it as training data for an RNN - you can keep it simple and train character level, and that is suggested as an initial approach.

Then, use that trained RNN to generate Shakespearean-ish text. Your goal - a function that can take, as an argument, the size of text (e.g. number of characters or lines) to generate, and returns generated text of that size.

Note - Shakespeare wrote an awful lot. It's OK, especially initially, to sample/use smaller data and parameters, so you can have a tighter feedback loop when you're trying to get things running. Then, once you've got a proof of concept - start pushing it more!

In [1]:
path = "shakespeare_text.txt"
with open(path, 'r') as f:
    content = f.read()

In [2]:
# Checking length of full content
len(content)

5584464

In [3]:
# Subsetting data for faster prototyping
subset = content[:100000]

In [4]:
# Checking that subset has appropriate length
len(subset)

100000

In [5]:
import numpy as np

data = subset

chars = list(set(data))

num_chars = len(chars)
txt_data_size = len(content)

print("unique characters : ", num_chars)



unique characters :  78


In [6]:
char_to_int = dict((c, i) for i, c in enumerate(chars))
int_to_char = dict((i, c) for i, c in enumerate(chars))
print(char_to_int)
print("-----------------------------------")
print(int_to_char)
print("-----------------------------------")

integer_encoded = [char_to_int[i] for i in data]

print('-----------------------------------')
print("data length : ", len(integer_encoded))

{'j': 0, '1': 1, '(': 2, '5': 3, 'P': 4, 'h': 5, ' ': 6, '.': 7, '\ufeff': 8, 'c': 9, 'a': 10, 'X': 11, 't': 12, 'b': 13, 's': 14, '-': 15, 'V': 16, 'r': 17, 'H': 18, 'A': 19, ']': 20, 'z': 21, 'm': 22, 'F': 23, 'w': 24, 'n': 25, 'C': 26, 'M': 27, 'f': 28, '!': 29, 'p': 30, '\n': 31, 'q': 32, 'W': 33, 'v': 34, 'd': 35, 'g': 36, 'i': 37, '6': 38, 'N': 39, 'l': 40, '[': 41, 'O': 42, ';': 43, 'y': 44, '’': 45, 'u': 46, '8': 47, '‘': 48, '0': 49, '7': 50, ')': 51, '*': 52, 'L': 53, 'S': 54, '3': 55, '2': 56, 'U': 57, '9': 58, '4': 59, '?': 60, 'o': 61, 'K': 62, 'D': 63, 'Y': 64, '#': 65, 'R': 66, 'x': 67, 'J': 68, 'G': 69, 'k': 70, 'E': 71, 'T': 72, 'I': 73, ',': 74, 'B': 75, ':': 76, 'e': 77}
-----------------------------------
{0: 'j', 1: '1', 2: '(', 3: '5', 4: 'P', 5: 'h', 6: ' ', 7: '.', 8: '\ufeff', 9: 'c', 10: 'a', 11: 'X', 12: 't', 13: 'b', 14: 's', 15: '-', 16: 'V', 17: 'r', 18: 'H', 19: 'A', 20: ']', 21: 'z', 22: 'm', 23: 'F', 24: 'w', 25: 'n', 26: 'C', 27: 'M', 28: 'f', 29: '!',

In [7]:
# Hyperparameters
iteration = 10
sequence_length = 40
batch_size = round((txt_data_size / sequence_length)+0.5)
hidden_size = 500
learning_rate = 1e-1

# Model parameters

W_xh = np.random.rand(hidden_size, num_chars)*0.01
W_hh = np.random.rand(hidden_size, hidden_size)*0.01
W_hy = np.random.randn(num_chars, hidden_size)*0.01

b_h = np.zeros((hidden_size, 1))
b_y = np.zeros((num_chars, 1))

h_prev = np.zeros((hidden_size,1))

In [8]:
def forwardprop(inputs, targets, h_prev):
    xs, hs, ys, ps = {}, {}, {}, {}
    hs[-1] = np.copy(h_prev)
    loss = 0
    
    for t in range(len(inputs)):
        
        xs[t] = np.zeros((num_chars,1))
        xs[t][inputs[t]] = 1
        hs[t] = np.tanh(np.dot(W_xh, xs[t]) + np.dot(W_hh, hs[t-1]) + b_h)
        ys[t] = np.dot(W_hy, hs[t]) + b_y
        ps[t] = np.exp(ys[t]) / np.sum(np.exp(ys[t]))
        
        
        print(t)
        print('len(ps) : ', len(ps))
        print('len(targets) : ', len(targets))
        loss += -np.log(ps[t][targets[t],0])
        
    return loss, ps, hs, xs
    

In [9]:
def backprop(ps, inputs, hs, xs, targets):
    
    dWxh, dWhh, dWhy = np.zeros_like(W_xh), np.zeros_like(W_hh), np.zeros_like(W_hy)
    dbh, dby = np.zeros_like(b_h), np.zeros_like(b_y)
    dhnext = np.zeros_like(hs[0])
    
    for t in reversed(range(len(inputs))):
        dy = np.copy(ps[t])
        dy[targets[t]] -= 1
        dWhy += np.dot(dy, hs[t].T)
        dby += dy
        dh = np.dot(W_hy.T, dy) + dhnext
        dhraw = (1 - hs[t] * hs[t]) * dh
        dbh += dhraw
        dWxh += np.dot(dhraw, xs[t].T)
        dWhh += np.dot(dhraw, hs[t-1].T)
        dhnext = np.dot(W_hh.T, dhraw)
    for dparam in[dWxh, dWhh, dWhy, dbh, dby]:
        np.clip(dparam, -5, 5, out=dparam)
        
    return dWxh, dWhh, dWhy, dbh, dby

In [12]:
# Training

# %%time

data_pointer = 0

mWxh, mWhh, mWhy = np.zeros_like(W_xh), np.zeros_like(W_hh), np.zeros_like(W_hy)
mbh, mby = np.zeros_like(b_h), np.zeros_like(b_y)

for i in range(iteration):
    h_prev = np.zeros((hidden_size,1))
    data_pointer = 0
    
    for b in range(batch_size):
        
        inputs = [char_to_int[ch] for ch in data[data_pointer:data_pointer+sequence_length]]
        targets = [char_to_int[ch] for ch in data[data_pointer+1:data_pointer+sequence_length+1]]
        
        if (data_pointer+sequence_length+1 >= len(data) and b == batch_size-1):
            targets.append(char_to_int[" "])
            
        loss, ps, hs, xs = forwardprop(inputs, targets, h_prev)
        
        dWxh, dWhh, dWhy, dbh, dby = backprop(ps, inputs, hs, xs, targets)
        
        
        for param, dparam, mem in zip([W_xh, W_hh, W_hy, b_h, b_y],
                                     [dWxh, dWhh, dWhy, dbh, dby],
                                     [mWxh, mWhh, mWhy, mbh, mby]):
            mem += dparam * dparam
            param += -learning_rate * dparam / np.sqrt(mem + 1e-8)
            
        data_pointer += sequence_length
        
    if i % 100 == 0:
        print( 'iter %d, loss: %f' % (i, loss))

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) :  29
len(targets) :  40
29
len(ps) :  30
len(targets) :  40
30
len(ps) :  31
len(t

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

...

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

0
len(ps) :  1
len(targets) :  40
1
len(ps) :  2
len(targets) :  40
2
len(ps) :  3
len(targets) :  40
3
len(ps) :  4
len(targets) :  40
4
len(ps) :  5
len(targets) :  40
5
len(ps) :  6
len(targets) :  40
6
len(ps) :  7
len(targets) :  40
7
len(ps) :  8
len(targets) :  40
8
len(ps) :  9
len(targets) :  40
9
len(ps) :  10
len(targets) :  40
10
len(ps) :  11
len(targets) :  40
11
len(ps) :  12
len(targets) :  40
12
len(ps) :  13
len(targets) :  40
13
len(ps) :  14
len(targets) :  40
14
len(ps) :  15
len(targets) :  40
15
len(ps) :  16
len(targets) :  40
16
len(ps) :  17
len(targets) :  40
17
len(ps) :  18
len(targets) :  40
18
len(ps) :  19
len(targets) :  40
19
len(ps) :  20
len(targets) :  40
20
len(ps) :  21
len(targets) :  40
21
len(ps) :  22
len(targets) :  40
22
len(ps) :  23
len(targets) :  40
23
len(ps) :  24
len(targets) :  40
24
len(ps) :  25
len(targets) :  40
25
len(ps) :  26
len(targets) :  40
26
len(ps) :  27
len(targets) :  40
27
len(ps) :  28
len(targets) :  40
28
len(ps) 

IndexError: list index out of range

In [16]:
def predict(test_char, length):
    x = np.zeros((num_chars, 1))
    x[char_to_int[test_char]] = 1
    ixes = []
    h = np.zeros((hidden_size,1))
    
    for t in range(length):
        h = np.tanh(np.dot(W_xh, x) + np.dot(W_hh, h) + b_h)
        y = np.dot(W_hy, h) + b_y
        p = np.exp(y) / np.sum(np.exp(y))
        ix = np.random.choice(range(num_chars), p=p.ravel())
        x = np.zeros((num_chars, 1))
        x[ix] = 1
        ixes.append(ix)
    txt = test_char + ''.join(int_to_char[i] for i in ixes)
    print('----/n %s /n----' % (txt, ))

In [17]:
predict('T', 50)

----/n TniIo
s oFUt nea ed1Hiye nr8 sh da,roehn shd  td1so /n----


# Resources and Stretch Goals

## Stretch goals:
- Refine the training and generation of text to be able to ask for different genres/styles of Shakespearean text (e.g. plays versus sonnets)
- Train a classification model that takes text and returns which work of Shakespeare it is most likely to be from
- Make it more performant! Many possible routes here - lean on Keras, optimize the code, and/or use more resources (AWS, etc.)
- Revisit the news example from class, and improve it - use categories or tags to refine the model/generation, or train a news classifier
- Run on bigger, better data

## Resources:
- [The Unreasonable Effectiveness of Recurrent Neural Networks](https://karpathy.github.io/2015/05/21/rnn-effectiveness/) - a seminal writeup demonstrating a simple but effective character-level NLP RNN
- [Simple NumPy implementation of RNN](https://github.com/JY-Yoon/RNN-Implementation-using-NumPy/blob/master/RNN%20Implementation%20using%20NumPy.ipynb) - Python 3 version of the code from "Unreasonable Effectiveness"
- [TensorFlow RNN Tutorial](https://github.com/tensorflow/models/tree/master/tutorials/rnn) - code for training a RNN on the Penn Tree Bank language dataset
- [4 part tutorial on RNN](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/) - relates RNN to the vanishing gradient problem, and provides example implementation
- [RNN training tips and tricks](https://github.com/karpathy/char-rnn#tips-and-tricks) - some rules of thumb for parameterizing and training your RNN